## 📈 Stock Predictor - Transformer Model (Darts)
This notebook trains a Transformer model using the `darts` library to predict the next-day closing price.

In [1]:
# Parameters
ticker = "AAPL"

In [2]:
# Parameters
ticker = "TSLA"


In [3]:
import pandas as pd
from src.data.fetcher import fetch_data
from darts.models import TransformerModel
from darts import TimeSeries
from darts.dataprocessing.transformers import Scaler
from darts.metrics import rmse
import matplotlib.pyplot as plt
import os

/media/sp/SinisterPuppy/SP/sandy-sp/repos/art-of-data-analysis/projects/stock-quant-analysis/venv/lib/python3.12/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [4]:
# Fetch full historical data
df = fetch_data(ticker, period="max")
df = df.reset_index()
df['Date'] = pd.to_datetime(df['Date'], errors='coerce')
df = df.dropna(subset=['Date'])
df['Date'] = df['Date'].dt.tz_localize(None)  # ✅ Strip timezone
print('✅ Final dtype of Date:', df['Date'].dtype)

✅ Final dtype of Date: datetime64[ns]


In [5]:
# Convert to TimeSeries
series = TimeSeries.from_dataframe(
    df,
    time_col="Date",
    value_cols="Close",
    fill_missing_dates=True,
    freq="D"
)
scaler = Scaler()
series_scaled = scaler.fit_transform(series)

In [6]:
# Train-validation split
train, val = series_scaled.split_before(0.8)

In [7]:
# Define Transformer model
model = TransformerModel(
    input_chunk_length=30,
    output_chunk_length=1,
    n_epochs=100,
    model_name=f"transformer_{ticker}",
    random_state=42,
    save_checkpoints=True,
    force_reset=True
)

In [8]:
# Train the model
model.fit(train, verbose=True)

/media/sp/SinisterPuppy/SP/sandy-sp/repos/art-of-data-analysis/projects/stock-quant-analysis/venv/lib/python3.12/site-packages/torch/nn/modules/transformer.py:385: UserWarning: enable_nested_tensor is True, but self.use_nested_tensor is False because encoder_layer.self_attn.batch_first was not True(use batch_first for better inference performance)
  warnings.warn(
GPU available: False, used: False


TPU available: False, using: 0 TPU cores


HPU available: False, using: 0 HPUs



  | Name                | Type                | Params | Mode 
--------------------------------------------------------------------
0 | criterion           | MSELoss             | 0      | train
1 | train_criterion     | MSELoss             | 0      | train
2 | val_criterion       | MSELoss             | 0      | train
3 | train_metrics       | MetricCollection    | 0      | train
4 | val_metrics         | MetricCollection    | 0      | train
5 | encoder             | Linear              | 128    | train
6 | positional_encoding | _PositionalEncoding | 0      | train
7 | transformer         | Transformer         | 548 K  | train
8 | decoder             | Linear              | 65     | train
--------------------------------------------------------------------
548 K     Trainable params
0         Non-trainable params
548 K     Total params
2.195     Total estimated model params size (MB)
88        Modules in train mode
0         Modules in eval mode


Training: |                                                                                                                                                                               | 0/? [00:00<?, ?it/s]

...

Epoch 99: 100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 135/135 [00:11<00:00, 11.56it/s, train_loss=nan.0]

Epoch 99: 100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 135/135 [00:11<00:00, 11.55it/s, train_loss=nan.0]

`Trainer.fit` stopped: `max_epochs=100` reached.


Epoch 99: 100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 135/135 [00:11<00:00, 11.49it/s, train_loss=nan.0]

TransformerModel(output_chunk_shift=0, d_model=64, nhead=4, num_encoder_layers=3, num_decoder_layers=3, dim_feedforward=512, dropout=0.1, activation=relu, norm_type=None, custom_encoder=None, custom_decoder=None, input_chunk_length=30, output_chunk_length=1, n_epochs=100, model_name=transformer_TSLA, random_state=42, save_checkpoints=True, force_reset=True)

In [9]:
# Forecast
forecast = model.predict(n=len(val))
forecast_actual = scaler.inverse_transform(forecast)
val_actual = scaler.inverse_transform(val)

GPU available: False, used: False


TPU available: False, using: 0 TPU cores


HPU available: False, using: 0 HPUs


Predicting: |                                                                                                                                                                             | 0/? [00:00<?, ?it/s]

Predicting:   0%|                                                                                                                                                                         | 0/1 [00:00<?, ?it/s]

Predicting DataLoader 0:   0%|                                                                                                                                                            | 0/1 [00:00<?, ?it/s]

Predicting DataLoader 0: 100%|████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 1/1 [00:03<00:00,  0.30it/s]

Predicting DataLoader 0: 100%|████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 1/1 [00:03<00:00,  0.30it/s]

In [10]:
# Evaluate
error = rmse(val_actual, forecast_actual)
print(f"Test RMSE: {error:.2f}")

Test RMSE: nan


/media/sp/SinisterPuppy/SP/sandy-sp/repos/art-of-data-analysis/projects/stock-quant-analysis/venv/lib/python3.12/site-packages/darts/metrics/metrics.py:1406: RuntimeWarning: Mean of empty slice
  return np.nanmean(
/media/sp/SinisterPuppy/SP/sandy-sp/repos/art-of-data-analysis/projects/stock-quant-analysis/venv/lib/python3.12/site-packages/darts/metrics/metrics.py:374: RuntimeWarning: Mean of empty slice
  vals = component_reduction(vals, axis=COMP_AX)


In [11]:
# Plot
plt.figure(figsize=(10,6))
val_actual.plot(label="Actual")
forecast_actual.plot(label="Predicted")
plt.title(f"{ticker} - Actual vs Predicted")
plt.legend()
os.makedirs(f"artifacts/reports", exist_ok=True)
plt.savefig(f"artifacts/reports/{ticker}_actual_vs_predicted.png")
plt.show()

/tmp/ipykernel_76626/623507711.py:9: UserWarning: FigureCanvasAgg is non-interactive, and thus cannot be shown
  plt.show()


In [12]:
# Save model and scaler
import joblib 

os.makedirs("artifacts/models", exist_ok=True)
model.save(f"artifacts/models/transformer_{ticker}.pt")
joblib.dump(scaler, f"artifacts/models/scaler_{ticker}.pkl")

['artifacts/models/scaler_TSLA.pkl']